# Kickstarter 2018 Decision Tree

May 28, 2019

Made by: Cristian E. Nuno

In [11]:
import collections
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import OneHotEncoder
from IPython.display import Image  
from sklearn import tree
import pydotplus
import pandas as pd
import numpy as np

In [2]:
df_2018 = pd.read_csv("raw_data/ks-projects-201801.csv")
df_2018.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 378661 entries, 0 to 378660
Data columns (total 15 columns):
ID                  378661 non-null int64
name                378657 non-null object
category            378661 non-null object
main_category       378661 non-null object
currency            378661 non-null object
deadline            378661 non-null object
goal                378661 non-null float64
launched            378661 non-null object
pledged             378661 non-null float64
state               378661 non-null object
backers             378661 non-null int64
country             378661 non-null object
usd pledged         374864 non-null float64
usd_pledged_real    378661 non-null float64
usd_goal_real       378661 non-null float64
dtypes: float64(5), int64(2), object(8)
memory usage: 43.3+ MB


Remove weird rows, because they're not important for our model.

In [3]:
#Detects the live in state and drops them 
df_2018 = df_2018.loc[df_2018['state']!='live']

#Detects the undefined in state and drops them 
df_2018 = df_2018.loc[df_2018['state']!='undefined']

#Detects the undefined in usd pledged and drops them 
df_2018 = df_2018.loc[~df_2018['usd pledged'].isna(), :]

#Detects the undefined in usd pledged and drops them 
df_2018 = df_2018.loc[~df_2018['name'].isna(), :]

df_2018.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 372062 entries, 0 to 378660
Data columns (total 15 columns):
ID                  372062 non-null int64
name                372062 non-null object
category            372062 non-null object
main_category       372062 non-null object
currency            372062 non-null object
deadline            372062 non-null object
goal                372062 non-null float64
launched            372062 non-null object
pledged             372062 non-null float64
state               372062 non-null object
backers             372062 non-null int64
country             372062 non-null object
usd pledged         372062 non-null float64
usd_pledged_real    372062 non-null float64
usd_goal_real       372062 non-null float64
dtypes: float64(5), int64(2), object(8)
memory usage: 45.4+ MB


In [4]:
X_train, X_test, y_train, y_test = train_test_split(df_2018.drop("state", axis=1),
                                                    df_2018["state"],
                                                    test_size=0.25,
                                                    random_state=2019)

Cleaning of the `state` feature

In [5]:
def change_state(series):
    return series.replace("canceled", "failed").replace("suspended", "failed")

In [6]:
y_train[:5]

71344     successful
109623      canceled
176999        failed
11711     successful
190406        failed
Name: state, dtype: object

In [7]:
change_state(y_train)[:5]

71344     successful
109623        failed
176999        failed
11711     successful
190406        failed
Name: state, dtype: object

In [8]:
y_train = change_state(y_train)
y_test = change_state(y_test)

In [9]:
y_train.value_counts(), y_test.value_counts()

(failed        178842
 successful    100204
 Name: state, dtype: int64, failed        59369
 successful    33647
 Name: state, dtype: int64)

## One Hot Encoding

In [10]:
X_train.head()

ID                                               name  \
71344   1363289603                                    MAGIC BULLET #3   
109623  1556995310  Zentangle Inspired Holiday Cards for Christmas...   
176999  1900400117                               Bitch or Best Friend   
11711   1058745576                   GrownUp KidStuff Chocolate Sauce   
190406  1969065891  Boutique Burger Bar: a hip & eco-friendly neig...   

            category main_category currency    deadline     goal  \
71344         Comics        Comics      USD  2011-08-15    600.0   
109623  Illustration           Art      GBP  2014-11-02    500.0   
176999    Nonfiction    Publishing      USD  2013-01-03   1800.0   
11711           Food          Food      USD  2013-04-04  12000.0   
190406          Food          Food      USD  2010-10-18  32500.0   

                   launched  pledged  backers country  usd pledged  \
71344   2011-06-21 15:40:18    681.0       32      US       681.00   
109623  2014-09-23 10:23:44    258.0       18      GB       421.82   
176999  2012-12-24 02:23:16      0.0        0      US         0.00   
11711   2013-03-05 00:41:26  13280.0      190      US     13280.00   
190406  2010-08-10 10:17:49    200.0        2      US       200.00   

        usd_pledged_real  usd_goal_real  
71344             681.00         600.00  
109623            408.14         790.98  
176999              0.00        1800.00  
11711           13280.00       12000.00  
190406            200.00       32500.00

In [12]:
encoder = OneHotEncoder(drop="first", categories="auto").fit(X_train[["category", "main_category", "country"]])

In [13]:
encoder.categories_

[array(['3D Printing', 'Academic', 'Accessories', 'Action', 'Animals',
        'Animation', 'Anthologies', 'Apparel', 'Apps', 'Architecture',
        'Art', 'Art Books', 'Audio', 'Bacon', 'Blues', 'Calendars',
        'Camera Equipment', 'Candles', 'Ceramics', "Children's Books",
        'Childrenswear', 'Chiptune', 'Civic Design', 'Classical Music',
        'Comedy', 'Comic Books', 'Comics', 'Community Gardens',
        'Conceptual Art', 'Cookbooks', 'Country & Folk', 'Couture',
        'Crafts', 'Crochet', 'DIY', 'DIY Electronics', 'Dance', 'Design',
        'Digital Art', 'Documentary', 'Drama', 'Drinks',
        'Electronic Music', 'Embroidery', 'Events', 'Experimental',
        'Fabrication Tools', 'Faith', 'Family', 'Fantasy',
        "Farmer's Markets", 'Farms', 'Fashion', 'Festivals', 'Fiction',
        'Film & Video', 'Fine Art', 'Flight', 'Food', 'Food Trucks',
        'Footwear', 'Gadgets', 'Games', 'Gaming Hardware', 'Glass',
        'Graphic Design', 'Graphic Novels', 'Har

In [14]:
ohe = pd.DataFrame(encoder.transform(X_train[["category", "main_category", "country"]]).toarray(),
                   columns=encoder.get_feature_names(["category", "main_category", "country"]))
ohe.head()

category_Academic  category_Accessories  category_Action  category_Animals  \
0                0.0                   0.0              0.0               0.0   
1                0.0                   0.0              0.0               0.0   
2                0.0                   0.0              0.0               0.0   
3                0.0                   0.0              0.0               0.0   
4                0.0                   0.0              0.0               0.0   

   category_Animation  category_Anthologies  category_Apparel  category_Apps  \
0                 0.0                   0.0               0.0            0.0   
1                 0.0                   0.0               0.0            0.0   
2                 0.0                   0.0               0.0            0.0   
3                 0.0                   0.0               0.0            0.0   
4                 0.0                   0.0               0.0            0.0   

   category_Architecture  category_Art     ...      country_IT  country_JP  \
0                    0.0           0.0     ...             0.0         0.0   
1                    0.0           0.0     ...             0.0         0.0   
2                    0.0           0.0     ...             0.0         0.0   
3                    0.0           0.0     ...             0.0         0.0   
4                    0.0           0.0     ...             0.0         0.0   

   country_LU  country_MX  country_NL  country_NO  country_NZ  country_SE  \
0         0.0         0.0         0.0         0.0         0.0         0.0   
1         0.0         0.0         0.0         0.0         0.0         0.0   
2         0.0         0.0         0.0         0.0         0.0         0.0   
3         0.0         0.0         0.0         0.0         0.0         0.0   
4         0.0         0.0         0.0         0.0         0.0         0.0   

   country_SG  country_US  
0         0.0         1.0  
1         0.0         0.0  
2         0.0         1.0  
3         0.0         1.0  
4         0.0         1.0  

[5 rows x 193 columns]

In [15]:
X_train.shape

(279046, 14)

In [16]:
ohe.shape

(279046, 193)

## Let's make a Decision Tree Classifier!

In [17]:
clf = DecisionTreeClassifier(random_state=2019,
                             min_samples_leaf=30,
                             criterion="gini",
                             min_samples_split=2)

clf.fit(ohe, y_train)

DecisionTreeClassifier(class_weight=None, criterion='gini', max_depth=None,
                       max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=30, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort=False,
                       random_state=2019, splitter='best')

In [19]:
# Create DOT data
dot_data = tree.export_graphviz(clf, 
                                out_file=None, 
                                feature_names=ohe.columns,  
                                class_names=["failed", "successful"])

# Draw graph
graph = pydotplus.graph_from_dot_data(dot_data)  

# Show graph
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.779628 to fit



## Feedback!

There are way too many features here to be of use to us. Let's do some PCA to figure out which features are worth keeping.